***
##### This notebook demonstrates how to place processing requests with the ESPA API. <br> We have created scene lists (text files) for the campaign, and made them accessible <br> over HTTP (defined below).
##### Through the ESPA API you can place orders, check on order status, and check on <br> individual scene processing status.
##### The download url to retrieve your products will be part of the response to <br>the '/item-status/' request (documented below), once processing completes <br>successfully for that scene
##### ESPA will email you with order details when you place an order, and once it completes. <br> <br> Please download your products as soon as they are complete, and let us know when <br> you download all the products for the order so that we can free up the space on our <br> storage device.
##### ESPA will automatically delete an orders products 10 days after completion, but we do <br> not have space to store the entire campaign over Africa all at once.
##### The notebook currently expects you to set your ERS https://ers.cr.usgs.gov/ credentials <br> in the environment in order to interact with the ESPA API.
***

#### Import Dependencies

In [ ]:
from copy import deepcopy
import json
import os
import re
import requests
from pprint import pprint

#### Capture ERS credentials

In [ ]:
#<your ERS username>
username = os.environ.get('USERNAME')

#<your ERS password>
pwd = os.environ.get('PASSWORD')

#### Hosts we'll be making requests to

In [ ]:
api_url = "https://espa.cr.usgs.gov/api/v1"

lists_url = "https://edclpdsftp.cr.usgs.gov/downloads/ga_sansa/"

#### Functions for handling requests to the ESPA API

In [ ]:
def apiget(resource, host=api_url, data=None):
    url = host+resource
    if data:
        r = requests.get(url, data=json.dumps(data), auth=(username, pwd))
    else:
        r = requests.get(url, auth=(username, pwd))
        
    return r.json()

def apipost(resource, data, host=api_url):
    url = host+resource
    r = requests.post(url, data=json.dumps(data), auth=(username, pwd))
    return r.json()

#### Test your connection to the ESPA API

In [ ]:
# view your user info
pprint(apiget("/user"))

#### Retrieve the names of the scene list files


##### The scene lists at the 'lists_url' location include all of the scene ids for the campaign over Africa

In [ ]:
scene_lists_request = requests.get(lists_url).text
list_names = re.findall(r'p[0-9]{3}[r0-9]{0,3}_scenes.txt', scene_lists_request)
list_names = set(list_names)

pprint(len(list_names))

print("This is a sub-set of the list names")
list(list_names)[0:5]

In [ ]:
def build_order_json(available_products):
    """
    Returns a collection ofvalid ESPA order json, based on the 
    available-products request response.
    The only product ordered is Aquatic Reflectance, and the output 
    format is set to COG.
    """
    orders = []
    for sensor in available_products:
        _order = dict()
        _order[sensor] = available_products[sensor]
        _order[sensor]['products'] = ['aq_refl']
        _order['format'] = 'cog'
        orders.append(_order)

    return orders    

def submit_order(order_json):
    """
    Submits the http POST request to place an Order with ESPA
    """
    order_response = apipost("/order", order_json)
    orderid = None
    if order_response.status_code == 200:
        orderid = order_response.get('orderid')
    else:
        print('Failed to submit order! reason: {}'.format(order_response.reason))

    return orderid

def process_list(list_name):
    """
    Returns a collection of order json organized by sensor.
    Some of the lists contain more than 10000 ids, and ESPA
    imposes a 10000 id limit per order. By organizing orders
    by sensor, we shouldn't have to worry about the per order
    scene limit restriction. 
    """
    # read in the ids from the list
    list_text = requests.get(lists_url+list_name)
    ids = [i for i in list_text.text.split('\r\n') if i]

    available_products = apiget("/available-products", data={'inputs': ids})
    order_json = build_order_json(available_products)
    return order_json


#### Demonstration for placing an Order and checking on its status

In [ ]:
# process_list returns a list of valid order json based on the
# contents of the scene list provided
demo_orders = process_list('p185_scenes.txt')

# grab the first order from the list, we're going to shorten it
test_order = deepcopy(demo_orders[0])

#### We're going to truncate the inputs for the demonstration

In [ ]:
test_order['olitirs8_collection_2_l1']['inputs'] = ['LC08_L1GT_185036_20200110_20200824_02_T2', 
                                                    'LC08_L1GT_185037_20200110_20200823_02_T2', 
                                                    'LC08_L1TP_185038_20200110_20200823_02_T1']

# the process_list function will return orders were 'cog' is the output format, at the time
# of writing though, this option is not yet available in production
test_order['format'] = 'gtiff'
pprint(test_order)

#### Place the order

In [ ]:
order_resp = apipost("/order", test_order)
pprint(order_resp)

#### Check on the orders status with a GET request to "/order/<orderid>" , 
#### the orderid is part of the response to the POST request when you submit the order 

In [ ]:
orderid = order_resp['orderid']
pprint(apiget("/order/"+orderid))

##### You can make GET requests to: '/item-status/<orderid>' to check on the status of the scenes in your order

In [ ]:
pprint(apiget("/item-status/"+orderid))

#### It's up to you to decide how you want to keep track of which scene lists have been ordered, and the rate at which you place your orders.
#### ESPA currently restricts users to 10,000 unprocessed scenes at a time.  
#### Once your scenes start completing, you can place additional orders.
#### You do not have to wait for an entire order to complete to start downloading products.